### RECEIVING DATA

In [2]:
import urllib.request
import json
import pandas as pd

In [3]:
import calendar

start_year = 2003
end_year = 2023

day_of_month_values = []
corresponding_months = []
corresponding_years = []

for year in range(start_year, end_year):
    for month in range(1, 13):
        last_day = calendar.monthrange(year, month)[1]
        days_of_month = list(range(1, last_day + 1))
        day_of_month_values.extend(days_of_month)
        corresponding_months.extend([calendar.month_name[month]] * last_day)
        corresponding_years.extend([year] * last_day)

# Provided data doesn't exist leap years
filtered_values = [
    (day, month, year)
    for day, month, year in zip(day_of_month_values, corresponding_months, corresponding_years)
    if not (day == 29 and month == 'February')
]

day_of_month_values, corresponding_months, corresponding_years = zip(*filtered_values)  # Unpack the filtered data

day_of_month_values = list(day_of_month_values)
corresponding_months = list(corresponding_months)
corresponding_years = list(corresponding_years)

print("Day-of-Month Values (Filtered):", type(day_of_month_values), len(day_of_month_values))
print("Corresponding Months (Filtered):", type(corresponding_months), len(day_of_month_values))
print("Corresponding Years (Filtered):", type(corresponding_years), len(corresponding_years))

Day-of-Month Values (Filtered): <class 'list'> 7300
Corresponding Months (Filtered): <class 'list'> 7300
Corresponding Years (Filtered): <class 'list'> 7300


In [4]:
import ssl
miet_ssl = ssl._create_unverified_context()  # ignore the ssl sertifiacte becayse of the original university SSL certificate

source_df = pd.DataFrame()
values = pd.DataFrame()

source_df['Date'] = day_of_month_values
source_df['Month'] = corresponding_months
source_df['Year'] = corresponding_years

for i in range(1, 14):
    with urllib.request.urlopen('https://dt.miet.ru/spinteh/api/' + str(i), context = miet_ssl) as url:
        city_data = json.load(url)
    source_df[city_data['message']['name']] = city_data['message']['data']
source_df

Date     Month  Year  Садовый  Курортный  Степной  Лесной  Научный  \
0        1   January  2003    -0.20       3.80    -5.30   -4.70   -20.10   
1        2   January  2003    -3.70       3.60    -3.00   -7.60   -16.30   
2        3   January  2003    -3.20       2.40    -6.90  -11.60   -17.10   
3        4   January  2003    -3.10       2.20   -20.80   -4.90   -18.70   
4        5   January  2003    -0.60       1.40   -20.60   -0.60   -20.30   
...    ...       ...   ...      ...        ...      ...     ...      ...   
7295    27  December  2022   -20.87      17.42   -15.00   -7.39   -18.21   
7296    28  December  2022   -18.67      17.02    -7.99   -7.80   -11.31   
7297    29  December  2022   -17.27      16.22    -3.28   -9.51    -5.81   
7298    30  December  2022   -12.87      15.92    -7.28   -1.91    -8.61   
7299    31  December  2022    -9.07      15.32    -4.07   -3.22   -10.21   

      Приморский  Северный  Западный  Таежный  Портовый  Алмазный  Полярный  \
0           0.60      0.50     -4.30   -10.70      5.10    -13.60    -14.00   
1           1.30     -2.30     -5.70   -11.70      6.80    -11.70     -8.20   
2           1.80     -1.20     -9.30   -18.70      8.10    -13.20     -7.50   
3           0.20      1.00     -5.40   -14.20      5.90    -12.80     -9.30   
4          -2.20      2.90     -5.20   -14.20      7.10    -10.70    -10.40   
...          ...       ...       ...      ...       ...       ...       ...   
7295        1.29      2.27    -14.39    -7.22     13.27    -13.72    -19.08   
7296        3.90      3.18    -17.10    -9.21     17.88    -14.02    -18.38   
7297        7.61      3.28     -6.41   -10.51      9.38    -10.42    -25.58   
7298        8.81      4.39     -4.71   -10.20      9.99     -0.92    -17.38   
7299        9.32      4.89     -5.82    -5.60     10.59     -3.22     -4.98   

      Южный  
0     -1.10  
1     -0.40  
2     -1.50  
3      0.30  
4      1.60  
...     ...  
7295   5.79  
7296   5.60  
7297   5.41  
7298   5.51  
7299   5.52  

[7300 rows x 16 columns]

In [5]:
# DataFrame to CSV
source_df.to_csv('source_df.csv', index=False)

### FILTERING DATA

In [6]:
import matplotlib.pyplot as plt
import plotly.express as px
import plotly
import plotly.graph_objs as go
import plotly.express as px
from plotly.subplots import make_subplots

In [7]:
# Graph before preprocessing

pd.options.plotting.backend = "plotly"
fig = source_df['Алмазный'].plot()
fig.show()

In [8]:
# Implementing Exponential Moving Average filtering
filtered_df = source_df.copy(deep=True)

alpha = 0.15  # the less the resent
threshold = 15

for city in filtered_df.columns[3:]:
    column = str(city+'_EMA')
    filtered_df[column] = filtered_df[city].ewm(alpha=alpha, adjust=False).mean()

    filtered_df['Is_Outlier'] = abs(filtered_df[city] - filtered_df[column]) > threshold
    filtered_df.loc[filtered_df['Is_Outlier'], city] = filtered_df.loc[filtered_df['Is_Outlier'], column]  # replace ouliers
    filtered_df.drop([column, 'Is_Outlier'], axis=1, inplace=True)
    
filtered_df

Date     Month  Year  Садовый  Курортный  Степной  Лесной  Научный  \
0        1   January  2003    -0.20       3.80    -5.30   -4.70   -20.10   
1        2   January  2003    -3.70       3.60    -3.00   -7.60   -16.30   
2        3   January  2003    -3.20       2.40    -6.90  -11.60   -17.10   
3        4   January  2003    -3.10       2.20   -20.80   -4.90   -18.70   
4        5   January  2003    -0.60       1.40   -20.60   -0.60   -20.30   
...    ...       ...   ...      ...        ...      ...     ...      ...   
7295    27  December  2022   -20.87      17.42   -15.00   -7.39   -18.21   
7296    28  December  2022   -18.67      17.02    -7.99   -7.80   -11.31   
7297    29  December  2022   -17.27      16.22    -3.28   -9.51    -5.81   
7298    30  December  2022   -12.87      15.92    -7.28   -1.91    -8.61   
7299    31  December  2022    -9.07      15.32    -4.07   -3.22   -10.21   

      Приморский  Северный  Западный  Таежный  Портовый  Алмазный  Полярный  \
0           0.60      0.50     -4.30   -10.70      5.10    -13.60    -14.00   
1           1.30     -2.30     -5.70   -11.70      6.80    -11.70     -8.20   
2           1.80     -1.20     -9.30   -18.70      8.10    -13.20     -7.50   
3           0.20      1.00     -5.40   -14.20      5.90    -12.80     -9.30   
4          -2.20      2.90     -5.20   -14.20      7.10    -10.70    -10.40   
...          ...       ...       ...      ...       ...       ...       ...   
7295        1.29      2.27    -14.39    -7.22     13.27    -13.72    -19.08   
7296        3.90      3.18    -17.10    -9.21     17.88    -14.02    -18.38   
7297        7.61      3.28     -6.41   -10.51      9.38    -10.42    -25.58   
7298        8.81      4.39     -4.71   -10.20      9.99     -0.92    -17.38   
7299        9.32      4.89     -5.82    -5.60     10.59     -3.22     -4.98   

      Южный  
0     -1.10  
1     -0.40  
2     -1.50  
3      0.30  
4      1.60  
...     ...  
7295   5.79  
7296   5.60  
7297   5.41  
7298   5.51  
7299   5.52  

[7300 rows x 16 columns]

In [9]:
# Adaptive Implementing Exponential Moving Average
#filtered_df = source_df.copy(deep=True)

#alpha = 0.2  # the less the resent

'''
thresholds = {
    'January': 15,
    'February': 15,
    'March': 10,
    'April': 8,
    'May': 8,
    'June': 8,
    'July': 8,
    'August': 5,
    'September': 5,
    'October': 8,
    'November': 8,
    'December': 10
}

for city in filtered_df.columns[3:]:
    column = city + '_EMA'
    filtered_df[column] = filtered_df[city].ewm(alpha=alpha, adjust=False).mean()
    month = filtered_df['Month'].iloc[0]
    
    if month in thresholds:
        is_outlier = abs(filtered_df[city] - filtered_df[column]) > thresholds[month]
        filtered_df.loc[is_outlier, city] = filtered_df.loc[is_outlier, column]
    
    filtered_df.drop([column], axis=1, inplace=True)
'''

"\nthresholds = {\n    'January': 15,\n    'February': 15,\n    'March': 10,\n    'April': 8,\n    'May': 8,\n    'June': 8,\n    'July': 8,\n    'August': 5,\n    'September': 5,\n    'October': 8,\n    'November': 8,\n    'December': 10\n}\n\nfor city in filtered_df.columns[3:]:\n    column = city + '_EMA'\n    filtered_df[column] = filtered_df[city].ewm(alpha=alpha, adjust=False).mean()\n    month = filtered_df['Month'].iloc[0]\n    \n    if month in thresholds:\n        is_outlier = abs(filtered_df[city] - filtered_df[column]) > thresholds[month]\n        filtered_df.loc[is_outlier, city] = filtered_df.loc[is_outlier, column]\n    \n    filtered_df.drop([column], axis=1, inplace=True)\n"

In [10]:
# Graph after filtering

pd.options.plotting.backend = "plotly"
fig = filtered_df['Алмазный'].plot()
fig.show()

In [11]:
# Overlay 'before' graph on the 'after'

for col in source_df.columns[3:]:
  fig = go.Figure()
  fig.add_trace(go.Scatter( x = source_df.index, y=source_df[col]))
  fig.add_trace(go.Scatter( x = source_df.index, y=filtered_df[col]))
  fig.update_layout(legend_orientation="h")
  fig.show()

In [12]:
# CSV-ing filtered FULL data

filtered_df.to_csv('filtered_df.csv', index=False)  # 20 years of filtered data

In [15]:
# Filtered 2022 year data

one_year_test_data = pd.DataFrame()
filtered_df_2022 = filtered_df[filtered_df['Year'] == 2022].copy()

filtered_df_2022

Date     Month  Year  Садовый  Курортный  Степной  Лесной  Научный  \
6935     1   January  2022    -5.01       9.70    -3.89   -6.00   -13.68   
6936     2   January  2022    -8.51       9.50    -1.59   -8.90   -10.78   
6937     3   January  2022    -8.01       8.30    -5.48  -12.91    -4.18   
6938     4   January  2022    -7.91       8.10   -19.37   -6.22    -5.48   
6939     5   January  2022    -5.41       7.30   -19.17   -1.92    -8.98   
...    ...       ...   ...      ...        ...      ...     ...      ...   
7295    27  December  2022   -20.87      17.42   -15.00   -7.39   -18.21   
7296    28  December  2022   -18.67      17.02    -7.99   -7.80   -11.31   
7297    29  December  2022   -17.27      16.22    -3.28   -9.51    -5.81   
7298    30  December  2022   -12.87      15.92    -7.28   -1.91    -8.61   
7299    31  December  2022    -9.07      15.32    -4.07   -3.22   -10.21   

      Приморский  Северный  Западный  Таежный  Портовый  Алмазный  Полярный  \
6935        2.00      5.25     -5.60    -5.94      9.85     -8.68     -9.71   
6936        2.70      2.45     -7.00    -6.94     11.55     -6.78     -3.91   
6937        3.21      3.56    -10.61   -13.93     12.86     -8.28     -3.21   
6938        1.62      5.76     -6.72    -9.43     10.66     -7.88     -5.01   
6939       -0.77      7.67     -6.52    -9.42     11.87     -5.78     -6.11   
...          ...       ...       ...      ...       ...       ...       ...   
7295        1.29      2.27    -14.39    -7.22     13.27    -13.72    -19.08   
7296        3.90      3.18    -17.10    -9.21     17.88    -14.02    -18.38   
7297        7.61      3.28     -6.41   -10.51      9.38    -10.42    -25.58   
7298        8.81      4.39     -4.71   -10.20      9.99     -0.92    -17.38   
7299        9.32      4.89     -5.82    -5.60     10.59     -3.22     -4.98   

      Южный  
6935   0.30  
6936   1.00  
6937  -0.08  
6938   1.72  
6939   3.02  
...     ...  
7295   5.79  
7296   5.60  
7297   5.41  
7298   5.51  
7299   5.52  

[365 rows x 16 columns]

In [16]:
filtered_df_2022.to_csv('filtered_df_2022.csv', index=False)  # 2022 year of filtered data